## Merge the annotations for sampled images

In [ ]:
import os
import json

# Turn the "dict" json into a "list" json
# We just need this json for one seed like local_seed_0 as we can use string.replace(..) to get the other samples' paths
base_dir = os.path.join("...")
seed = os.path.join(base_dir, "local_seed_0")
out_dir = os.path.join(base_dir, "annotations")


In [ ]:

results = []
for file in os.listdir(os.path.join(seed, "annotations")):
    if file.endswith(".json"):
        print(f"Processing {file} in {os.path.join(seed, "annotations")}")
        with open(os.path.join(os.path.join(seed, "annotations"), file), "r") as f:
            data = json.load(f)

        for k, v in data.items():
            v["image_id"] = k
            results.append(v)


In [ ]:
os.makedirs(out_dir, exist_ok=True)
with open(os.path.join(out_dir, "results.json"), "w") as f:
    json.dump(results, f, indent=2)

## Format the vllm results

### For vllm resample if there's network error

In [5]:
import os
import json
import re
base_dirs =["/root/flux/runs/scores/idream/brushnet/unified_reward"]
out_dir = "/root/BrushNet/runs/samples/idream/global_seed_42/annotations"
seeds = list(range(0,16))


In [6]:
with open(os.path.join("/root/BrushNet/runs/samples/idream/global_seed_42/annotations/results_list_1k.json"), 'r') as f:
    annotations_list = json.load(f)
    
all_annotations = {}
for item in annotations_list:
    all_annotations[f"{item["image_id"]}"] = item

In [7]:
resamples = []
for base_dir in base_dirs:
    for seed in seeds:
        score_files = os.listdir(os.path.join(base_dir, f"local_seed_{seed}", "unified_reward")) 
        score_files = sorted(score_files) # always process "vllm_results_0.json" first
        for score_file in score_files:
            if score_file.startswith("vllm_results") and score_file.endswith(".json"):
                if "batch_1" in base_dir and "new" not in score_file:
                    continue
                print(f"Processing {score_file} for seed {seed}")
                with open(os.path.join(base_dir, f"local_seed_{seed}", "unified_reward", score_file), 'r') as f:
                    for line in f:
                        line= line.strip()
                        if line:
                            record = json.loads(line)
                            if not record["success"] and "HTTPConnectionPool" not in record["error"] and "Server Error" not in record["error"]:
                                caption = all_annotations[record["image_id"]]["caption"]
                                resamples.append(
                                    {
                                        "image_id": record["image_id"],
                                        "image_path": record["image_path"][0],
                                        "caption": caption
                                    }
                                )

                    

Processing vllm_results_0.json for seed 0
Processing vllm_results_0.json for seed 1
Processing vllm_results_0.json for seed 2
Processing vllm_results_0.json for seed 3
Processing vllm_results_0.json for seed 4
Processing vllm_results_0.json for seed 5
Processing vllm_results_0.json for seed 6
Processing vllm_results_0.json for seed 7
Processing vllm_results_0.json for seed 8
Processing vllm_results_0.json for seed 9
Processing vllm_results_0.json for seed 10
Processing vllm_results_0.json for seed 11
Processing vllm_results_0.json for seed 12
Processing vllm_results_0.json for seed 13
Processing vllm_results_0.json for seed 14
Processing vllm_results_0.json for seed 15


In [ ]:
# you should use this json to rescore the failed cases
with open(os.path.join(out_dir, "resamples.json"), 'w') as f:
    json.dump(resamples, f, indent=2)

### Format vllm result

In [43]:
import os
vllm_score_dirs = ["/root/flux/runs/scores/idream/flux/unified_reward"]
seeds = [f"local_seed_{seed}" for seed in range(0, 16)] 
out_dir = "/root/flux/runs/scores/idream/flux/unified_reward"

# score_files = [os.path.join(vllm_score_dir, seed, "unified_reward", "vllm_results_0.json") if "batch_2" in vllm_score_dir else os.path.join(vllm_score_dir, seed, "unified_reward", "vllm_results_new.json") for vllm_score_dir in vllm_score_dirs for seed in seeds]
score_files = [os.path.join(vllm_score_dir, seed, "unified_reward", "vllm_results_0.json")  for vllm_score_dir in vllm_score_dirs for seed in seeds]
# score_files += ["/root/flux/runs/scores/flux/batch_all/unified_reward/resample/unified_reward/vllm_results_0_resampled.json"]

import json
from collections import defaultdict

In [44]:
score_files

['/root/flux/runs/scores/idream/flux/unified_reward/local_seed_0/unified_reward/vllm_results_0.json',
 '/root/flux/runs/scores/idream/flux/unified_reward/local_seed_1/unified_reward/vllm_results_0.json',
 '/root/flux/runs/scores/idream/flux/unified_reward/local_seed_2/unified_reward/vllm_results_0.json',
 '/root/flux/runs/scores/idream/flux/unified_reward/local_seed_3/unified_reward/vllm_results_0.json',
 '/root/flux/runs/scores/idream/flux/unified_reward/local_seed_4/unified_reward/vllm_results_0.json',
 '/root/flux/runs/scores/idream/flux/unified_reward/local_seed_5/unified_reward/vllm_results_0.json',
 '/root/flux/runs/scores/idream/flux/unified_reward/local_seed_6/unified_reward/vllm_results_0.json',
 '/root/flux/runs/scores/idream/flux/unified_reward/local_seed_7/unified_reward/vllm_results_0.json',
 '/root/flux/runs/scores/idream/flux/unified_reward/local_seed_8/unified_reward/vllm_results_0.json',
 '/root/flux/runs/scores/idream/flux/unified_reward/local_seed_9/unified_reward/vl

In [45]:
# 用于存储结果
results = defaultdict(dict)

def process_file(filename, results):
    with open(filename, 'r') as f:
        for line in f:
            if not line.strip():
                continue
            record = json.loads(line)

            image_id = record.get("image_id")
            if image_id.startswith("images_"):
                image_id = image_id[len("images_"):]
            if not image_id.endswith(".jpg"):
                image_id += ".jpg"
            image_paths = record.get("image_path", [])
            final_score = record.get("final_score", None)

            for path in image_paths:
                if "local_seed_" in path:
                    parts = path.split('/')
                    for part in parts:
                        if part.startswith("local_seed_"):
                            seed_number = part.replace("local_seed_", "")
                            seed_key = f"seed_{seed_number}"
                            # 覆盖写入
                            results[image_id][seed_key] = {"unified_reward": final_score}
                            break



In [46]:
results = defaultdict(dict)
for score_file in score_files:
    print(f"Processing {score_file}")
    process_file(score_file, results)

results = dict(results)  # Convert defaultdict to regular dict for JSON serialization

Processing /root/flux/runs/scores/idream/flux/unified_reward/local_seed_0/unified_reward/vllm_results_0.json
Processing /root/flux/runs/scores/idream/flux/unified_reward/local_seed_1/unified_reward/vllm_results_0.json
Processing /root/flux/runs/scores/idream/flux/unified_reward/local_seed_2/unified_reward/vllm_results_0.json
Processing /root/flux/runs/scores/idream/flux/unified_reward/local_seed_3/unified_reward/vllm_results_0.json
Processing /root/flux/runs/scores/idream/flux/unified_reward/local_seed_4/unified_reward/vllm_results_0.json
Processing /root/flux/runs/scores/idream/flux/unified_reward/local_seed_5/unified_reward/vllm_results_0.json
Processing /root/flux/runs/scores/idream/flux/unified_reward/local_seed_6/unified_reward/vllm_results_0.json
Processing /root/flux/runs/scores/idream/flux/unified_reward/local_seed_7/unified_reward/vllm_results_0.json
Processing /root/flux/runs/scores/idream/flux/unified_reward/local_seed_8/unified_reward/vllm_results_0.json
Processing /root/fl

In [47]:
for i in results:
    assert len(results[i]) == 16, f"Image {i} does not have scores for all seeds."

In [48]:
with open(os.path.join(out_dir, "scores_0.json"), 'w') as f:
    json.dump(results, f, indent=2)

## Merge all the scores into one file

In [49]:
import json
import os
score_base = os.path.join("/root/flux/runs/scores/idream/flux")
score_list = ['hps','vqa_score','clip_score','pick_score','aesthetic_score','image_reward', "unified_reward", "pe_score", "hpsv3"]
# score_list = ['hps']

In [50]:
def reorder_scores(original_dict):
    new_dict = {}

    for image_id, seeds in original_dict.items():
        new_dict[image_id] = {}
        for seed_id, score_dict in seeds.items():
            for score_type, score_value in score_dict.items():
                if score_type not in new_dict[image_id]:
                    new_dict[image_id][score_type] = {}
                new_dict[image_id][score_type][seed_id] = score_value

    return new_dict

In [51]:
def merge_score_dicts(dicts):
    merged = {}

    for d in dicts:
        for image_id, score_types in d.items():
            if image_id not in merged:
                merged[image_id] = {}

            for score_type, seed_scores in score_types.items():
                if score_type not in merged[image_id]:
                    merged[image_id][score_type] = {}

                merged[image_id][score_type].update(seed_scores)

    return merged


In [52]:
score_levels = []
for _score_list in score_list:
    score_level = {}
    for score_file in os.listdir(os.path.join(score_base, _score_list)):
        if score_file.endswith('.json'):
            print(f"Processing {score_file} in {_score_list}")
            with open(os.path.join(score_base, _score_list, score_file), 'r') as f:
                score_data = json.load(f)
                score_level.update(score_data)
    
    score_levels.append(reorder_scores(score_level))

merged_scores = merge_score_dicts(score_levels)

Processing scores_3.json in hps
Processing scores_5.json in hps
Processing scores_2.json in hps
Processing scores_0.json in hps
Processing scores_4.json in hps
Processing scores_1.json in hps
Processing scores_7.json in hps
Processing scores_6.json in hps
Processing scores_3.json in vqa_score
Processing scores_5.json in vqa_score
Processing scores_2.json in vqa_score
Processing scores_0.json in vqa_score
Processing scores_4.json in vqa_score
Processing scores_1.json in vqa_score
Processing scores_7.json in vqa_score
Processing scores_6.json in vqa_score
Processing scores_3.json in clip_score
Processing scores_5.json in clip_score
Processing scores_2.json in clip_score
Processing scores_0.json in clip_score
Processing scores_4.json in clip_score
Processing scores_1.json in clip_score
Processing scores_7.json in clip_score
Processing scores_6.json in clip_score
Processing scores_3.json in pick_score
Processing scores_5.json in pick_score
Processing scores_2.json in pick_score
Processing 

In [53]:
for i in merged_scores:
    assert len(merged_scores[i]) == len(score_list), f"Image {i} does not have all scores"
    for j in merged_scores[i]:
        assert len(merged_scores[i][j]) == 16, f"Image {i} does not have all seeds for score {j}"

In [ ]:
import copy
def add_min_max_with_seed_new(data: dict) -> dict:
    """
    Adds max and min values along with their corresponding seeds to the score dictionary.
    Returns a new dictionary without modifying the original input.
    """
    new_data = copy.deepcopy(data)

    for image_id, score_types in new_data.items():
        for score_type, seed_scores in score_types.items():
            # get all (seed, value) pairs where seed starts with "seed_"
            seed_value_pairs = [
                (seed, value)
                for seed, value in seed_scores.items()
                if seed.startswith("seed_") and isinstance(value, (int, float))
            ]

            if not seed_value_pairs:
                continue

            # extract seeds and values
            seeds, values = zip(*seed_value_pairs)

            # find indices of max and min values
            max_idx = values.index(max(values))
            min_idx = values.index(min(values))

            if max_idx == min_idx:
                seed_scores["draw"] = True
            else:
                seed_scores["draw"] = False
                
            # add max and min values with corresponding seeds
            seed_scores["max_value"] = values[max_idx]
            seed_scores["max_seed"] = seeds[max_idx]
            seed_scores["min_value"] = values[min_idx]
            seed_scores["min_seed"] = seeds[min_idx]

    return new_data

In [55]:
merged_scores_with_seed = add_min_max_with_seed_new(merged_scores)

In [56]:
os.makedirs(os.path.join(score_base, "result"), exist_ok=True)
with open(os.path.join(score_base, "result", "results.json"), 'w') as f:
    json.dump(merged_scores_with_seed, f, indent=2)


## Add extra scores (hpsv3)

In [17]:
import os
import json

new_scores_dir = "/root/flux/runs/scores/flux/batch_all/hpsv3"
cur_scores_file = "/root/flux/runs/scores/flux/batch_all/result/results.json"

new_scores = dict()
for file in os.listdir(new_scores_dir):
    if file.endswith(".json"):
        with open(os.path.join(new_scores_dir, file), "r") as f:
            scores = json.load(f)
            new_scores.update(scores)

with open(cur_scores_file, "r") as f:
    cur_scores = json.load(f)

for image_id in cur_scores:
    if image_id in new_scores:
        hps_v3 = dict()
        for seed in range(16):
            hps_v3[f"seed_{seed}"] = new_scores[image_id][f"seed_{seed}"]["hpsv3"]
        cur_scores[image_id]["hpsv3"] = hps_v3
    else:
        raise ValueError(f"Image ID {image_id} not found in new scores")


In [ ]:
import copy
def add_min_max_with_seed_new(data: dict, new_score_type:str="hpsv3") -> dict:
    """
    Adds max and min values along with their corresponding seeds to the score dictionary.
    Returns a new dictionary without modifying the original input.
    """
    new_data = copy.deepcopy(data)

    for image_id, score_types in new_data.items():            
        for score_type, seed_scores in score_types.items():
            # get all (seed, value) pairs where seed starts with "seed_"
            if new_score_type is not None:
                if score_type != new_score_type:
                    print(f"Skipping {score_type}")
                    continue
            seed_value_pairs = [
                (seed, value)
                for seed, value in seed_scores.items()
                if seed.startswith("seed_") and isinstance(value, (int, float))
            ]

            if not seed_value_pairs:
                continue

            # extract seeds and values
            seeds, values = zip(*seed_value_pairs)

            # find indices of max and min values
            max_idx = values.index(max(values))
            min_idx = values.index(min(values))

            if max_idx == min_idx:
                seed_scores["draw"] = True
            else:
                seed_scores["draw"] = False
                
            # add max and min values with corresponding seeds
            seed_scores["max_value"] = values[max_idx]
            seed_scores["max_seed"] = seeds[max_idx]
            seed_scores["min_value"] = values[min_idx]
            seed_scores["min_seed"] = seeds[min_idx]

    return new_data

In [19]:
new_scores_with_minmax = add_min_max_with_seed_new(cur_scores, "hpsv3")

Skipping hps
Skipping vqa_score
Skipping clip_score
Skipping pick_score
Skipping aesthetic_score
Skipping image_reward
Skipping unified_reward
Skipping pe_score
Skipping hps
Skipping vqa_score
Skipping clip_score
Skipping pick_score
Skipping aesthetic_score
Skipping image_reward
Skipping unified_reward
Skipping pe_score
Skipping hps
Skipping vqa_score
Skipping clip_score
Skipping pick_score
Skipping aesthetic_score
Skipping image_reward
Skipping unified_reward
Skipping pe_score
Skipping hps
Skipping vqa_score
Skipping clip_score
Skipping pick_score
Skipping aesthetic_score
Skipping image_reward
Skipping unified_reward
Skipping pe_score
Skipping hps
Skipping vqa_score
Skipping clip_score
Skipping pick_score
Skipping aesthetic_score
Skipping image_reward
Skipping unified_reward
Skipping pe_score
Skipping hps
Skipping vqa_score
Skipping clip_score
Skipping pick_score
Skipping aesthetic_score
Skipping image_reward
Skipping unified_reward
Skipping pe_score
Skipping hps
Skipping vqa_score
Sk

In [22]:
new_scores_with_minmax["00033_000333676"]["hpsv3"]

{'seed_0': 1.9492162466049194,
 'seed_1': 1.594447374343872,
 'seed_2': 1.6640931367874146,
 'seed_3': 1.6645151376724243,
 'seed_4': 1.9443004131317139,
 'seed_5': 1.9358311891555786,
 'seed_6': 1.4436770677566528,
 'seed_7': 1.691687822341919,
 'seed_8': 1.9121242761611938,
 'seed_9': 1.8328953981399536,
 'seed_10': 1.8862375020980835,
 'seed_11': 1.8775267601013184,
 'seed_12': 1.96470046043396,
 'seed_13': 1.6806368827819824,
 'seed_14': 1.9502671957015991,
 'seed_15': 1.5247570276260376,
 'draw': False,
 'max_value': 1.96470046043396,
 'max_seed': 'seed_12',
 'min_value': 1.4436770677566528,
 'min_seed': 'seed_6'}

In [24]:
with open(os.path.join("/root/flux/runs/scores/flux/batch_all/result/new_results.json"), 'w') as f:
    json.dump(new_scores_with_minmax, f, indent=2)

In [14]:
new_scores_with_minmax["00033_000333676"]["hpsv3"]

{'seed_0': 2.6869187355041504,
 'seed_1': 2.7406535148620605,
 'seed_2': 2.9443812370300293,
 'seed_3': 2.8857429027557373,
 'seed_4': 2.6048946380615234,
 'seed_5': 3.065488576889038,
 'seed_6': 2.5404677391052246,
 'seed_7': 2.6232690811157227,
 'seed_8': 2.8158318996429443,
 'seed_9': 2.4458823204040527,
 'seed_10': 2.870521306991577,
 'seed_11': 2.539916753768921,
 'seed_12': 2.709400177001953,
 'seed_13': 2.602675676345825,
 'seed_14': 2.659048080444336,
 'seed_15': 2.4777636528015137,
 'draw': False,
 'max_value': 3.065488576889038,
 'max_seed': 'seed_5',
 'min_value': 2.4458823204040527,
 'min_seed': 'seed_9'}

## Create ensemble score and rank

In [ ]:
import json
import os
from collections import Counter

base_dir = "/root/flux/runs/scores/idream/flux/result/results.json"
score_lists = ["hps","clip_score",  "pick_score", "aesthetic_score", "image_reward", "vqa_score", "unified_reward", "pe_score", "hpsv3"]

with open(base_dir, 'r') as f:
    data = json.load(f)

def rank_scores(scores: dict, descending: bool = True) -> dict:
    """
    - descending=True means higher scores get better ranks (rank=1 is best).
    - Ties are handled by "dense" method: same score same rank, the next rank is incremented by 1. i.e., 1, 2, 2, 3…
    Returns a dict of {key: rank}.
    """
    vals = list(scores.values())
    counts = Counter(vals)
    uniq_vals = sorted(counts.keys(), reverse=descending)

    value_to_rank = {}

    rank = 1
    for v in uniq_vals:
        value_to_rank[v] = rank
        rank += 1

    return {k: value_to_rank[v] for k, v in scores.items()}

for image_id, scores in data.items():
    for score_type in score_lists:
        sorted_seeds = sorted(
            ((k, v) for k, v in scores[score_type].items() if k.startswith("seed_")),
            key=lambda x: x[1],
            reverse=True
        )

        # print(sorted_seeds)

        # get the rank dict
        rank = rank_scores({seed: value for seed, value in sorted_seeds})
        if scores[score_type]["draw"]:
            rank = {seed: 0 for i, (seed, _) in enumerate(sorted_seeds)}
        assert len(rank) == 16, f"Image {image_id} does not have all seeds for score {score_type}"
        scores[score_type]["rank"] = rank


In [58]:
for image_id, scores in data.items():
    ensemble = {}
    for seed in range(16):
        for score_type in score_lists:
            ensemble[f"seed_{seed}"] = scores[score_type]["rank"].get(f"seed_{seed}") + ensemble.get(f"seed_{seed}", 0)

    scores["ensemble"] = ensemble

In [ ]:
import copy
def add_min_max_with_seed_new(data: dict) -> dict:
    """
    返回一个新的 dict，其中每个 score_type 增加 max_value/min_value 和对应 seed。
    不修改原始输入。
    """
    new_data = copy.deepcopy(data)
    import random
    random.seed(42)  

    for image_id, score_types in new_data.items():
        for score_type, seed_scores in score_types.items():
            if score_type != "ensemble":
                continue
            # get all (seed, value) pairs where seed starts with "seed_"
            seed_value_pairs = [
                (seed, value)
                for seed, value in seed_scores.items()
                if seed.startswith("seed_") and isinstance(value, (int, float))
            ]

            if not seed_value_pairs:
                print(f"No valid seed-value pairs found for {image_id} in {score_type}. Skipping.")
                continue

            # extract seeds and values
            seeds, values = zip(*seed_value_pairs)
            
            min_value = min(values)
            max_value = max(values)

            min_idxs = []
            max_idxs = []

            for i, value in enumerate(values):
                if value == min_value:
                    min_idxs.append(i)
                if value == max_value:
                    max_idxs.append(i)

            # the max_idx is idx with the minimum value because value here means the rank
            if len(min_idxs) > 1:
                print(f"Multiple minimum values ({len(min_idxs)}) found for {image_id} in {score_type}. Choosing randomly.")
                max_idx = random.choice(min_idxs)
            else:
                max_idx = values.index(min(values))

            if len(max_idxs) > 1:
                print(f"Multiple maximum values found ({len(max_idxs)}) for {image_id} in {score_type}. Choosing randomly.")
                min_idx = random.choice(max_idxs)
            else:
                min_idx = values.index(max(values))

            if max_idx == min_idx:
                seed_scores["draw"] = True
            else:
                seed_scores["draw"] = False
                
            # add max and min values with corresponding seeds
            seed_scores["max_value"] = values[max_idx]
            seed_scores["max_seed"] = seeds[max_idx]
            seed_scores["min_value"] = values[min_idx]
            seed_scores["min_seed"] = seeds[min_idx]

    return new_data

In [60]:
new_data = add_min_max_with_seed_new(data)

Multiple minimum values (2) found for theodor-severin-kittelsen_forest-troll-skogtrold.jpg in ensemble. Choosing randomly.
Multiple maximum values found (3) for maximilian-pirner_portrait-of-mikolas-ales.jpg in ensemble. Choosing randomly.
Multiple minimum values (2) found for oskar-kokoschka_not_detected_235935.jpg in ensemble. Choosing randomly.
Multiple minimum values (2) found for paul-cezanne_jas-de-bouffan-the-pool.jpg in ensemble. Choosing randomly.
Multiple minimum values (2) found for koloman-moser_church-am-steinhof-design-for-the-east-side-windows-1905.jpg in ensemble. Choosing randomly.
Multiple maximum values found (2) for walter-battiss_cape-winter.jpg in ensemble. Choosing randomly.
Multiple maximum values found (2) for ivan-bilibin_illustration-for-alexander-pushkin-s-fairytale-of-the-tsar-saltan-1905.jpg in ensemble. Choosing randomly.
Multiple maximum values found (2) for auguste-edouart_niccol-paganini-1835.jpg in ensemble. Choosing randomly.
Multiple maximum values 

In [61]:
with open(os.path.join("/root/flux/runs/scores/idream/flux/result/scores_with_ensemble.json"), 'w') as f:
    json.dump(new_data, f, indent=2)

In [63]:
new_data["gr-goire-michonze_in-the-village-1978.jpg"]

{'hps': {'seed_0': 0.2103271484375,
  'seed_1': 0.20947265625,
  'seed_2': 0.2110595703125,
  'seed_3': 0.199951171875,
  'seed_4': 0.2064208984375,
  'seed_5': 0.2139892578125,
  'seed_6': 0.2001953125,
  'seed_7': 0.204345703125,
  'seed_8': 0.214111328125,
  'seed_9': 0.213134765625,
  'seed_10': 0.2152099609375,
  'seed_11': 0.215087890625,
  'seed_12': 0.2081298828125,
  'seed_13': 0.214599609375,
  'seed_14': 0.2191162109375,
  'seed_15': 0.1993408203125,
  'draw': False,
  'max_value': 0.2191162109375,
  'max_seed': 'seed_14',
  'min_value': 0.1993408203125,
  'min_seed': 'seed_15',
  'rank': {'seed_14': 1,
   'seed_10': 2,
   'seed_11': 3,
   'seed_13': 4,
   'seed_8': 5,
   'seed_5': 6,
   'seed_9': 7,
   'seed_2': 8,
   'seed_0': 9,
   'seed_1': 10,
   'seed_12': 11,
   'seed_4': 12,
   'seed_7': 13,
   'seed_6': 14,
   'seed_3': 15,
   'seed_15': 16}},
 'vqa_score': {'seed_0': 0.887682318687439,
  'seed_1': 0.8933349847793579,
  'seed_2': 0.8985847234725952,
  'seed_3': 0.88

In [1]:
import os
import json
with open(os.path.join("/root/BrushNet/runs/hyper_para/annotations/scores_with_ensemble.json")) as f:
    data = json.load(f)

In [34]:
# new_data["00033_000333676"] 
new_data["00069_000690055"]

{'hps': {'seed_0': 0.1898193359375,
  'seed_1': 0.1934814453125,
  'seed_2': 0.1942138671875,
  'seed_3': 0.193603515625,
  'seed_4': 0.195556640625,
  'seed_5': 0.197509765625,
  'seed_6': 0.1927490234375,
  'seed_7': 0.1883544921875,
  'seed_8': 0.1961669921875,
  'seed_9': 0.1986083984375,
  'seed_10': 0.191162109375,
  'seed_11': 0.1956787109375,
  'seed_12': 0.193603515625,
  'seed_13': 0.204833984375,
  'seed_14': 0.1982421875,
  'seed_15': 0.188720703125,
  'draw': False,
  'max_value': 0.204833984375,
  'max_seed': 'seed_13',
  'min_value': 0.1883544921875,
  'min_seed': 'seed_7',
  'rank': {'seed_13': 1,
   'seed_9': 2,
   'seed_14': 3,
   'seed_5': 4,
   'seed_8': 5,
   'seed_11': 6,
   'seed_4': 7,
   'seed_2': 8,
   'seed_3': 9,
   'seed_12': 9,
   'seed_1': 10,
   'seed_6': 11,
   'seed_10': 12,
   'seed_0': 13,
   'seed_15': 14,
   'seed_7': 15}},
 'vqa_score': {'seed_0': 0.47236576676368713,
  'seed_1': 0.47236576676368713,
  'seed_2': 0.37513452768325806,
  'seed_3': 0.

## Create candidates scaling

In [ ]:
import json
import os
import random
with open("/root/BrushNet/runs/hyper_para/annotations/new_scores_with_ensemble.json", "r") as f:
    scores = json.load(f)
scalings = [2, 4, 8]
seeds = [f"seed_{i}" for i in range(0, 16)]
from copy import deepcopy
new_results = {}
step = 0
length = len(scores)
for key, value in scores.items():
    print(f"{step}/{length}")
    new_results[key] = {}
    ensemble = deepcopy(value["ensemble"])
    for scaling in scalings:
        min_idx = []
        max_idx = []
        temp = dict(zip(seeds[:scaling], [ensemble[seed] for seed in seeds[:scaling]]))
        min_seed = max(temp, key=temp.get) # modified here for ensemble, and other reward models
        max_seed = min(temp, key=temp.get) # modified here for ensemble, and other reward models
        for s, score in temp.items():
            if score == temp[min_seed]:
                min_idx.append(s)
            if score == temp[max_seed]:
                max_idx.append(s)
        if len(min_idx) > 1:
            print(f"Multiple minimum values ({len(min_idx)}) found for {key} in scaling {scaling}. Choosing randomly.")
            min_seed = random.choice(min_idx)
        if len(max_idx) > 1:
            print(f"Multiple maximum values found ({len(max_idx)}) for {key} in scaling {scaling}. Choosing randomly.")
            max_seed = random.choice(max_idx)
            while min_seed == max_seed:
                max_seed = random.choice(max_idx)
        ensemble[f"max_seed_{scaling}"] = max_seed
        ensemble[f"max_value_{scaling}"] = temp[max_seed]
        ensemble[f"min_seed_{scaling}"] = min_seed
        ensemble[f"min_value_{scaling}"] = temp[min_seed]
        # print(temp)
        # print(f"max: {max(temp, key=temp.get)}, min: {min(temp, key=temp.get)}")
    new_results[key]["ensemble"] = ensemble
    step += 1

0/128000
1/128000
2/128000
Multiple maximum values found (2) for 00038_000380718 in scaling 8. Choosing randomly.
3/128000
4/128000
5/128000
6/128000
7/128000
8/128000
9/128000
10/128000
11/128000
12/128000
13/128000
14/128000
Multiple maximum values found (2) for 00076_000761251 in scaling 8. Choosing randomly.
15/128000
Multiple minimum values (2) found for 00068_000685931 in scaling 2. Choosing randomly.
Multiple maximum values found (2) for 00068_000685931 in scaling 2. Choosing randomly.
Multiple maximum values found (2) for 00068_000685931 in scaling 4. Choosing randomly.
16/128000
17/128000
Multiple maximum values found (2) for 00039_000396799 in scaling 4. Choosing randomly.
18/128000
19/128000
20/128000
21/128000
22/128000
23/128000
24/128000
25/128000
26/128000
27/128000
28/128000
29/128000
30/128000
Multiple minimum values (2) found for 00079_000790309 in scaling 2. Choosing randomly.
Multiple maximum values found (2) for 00079_000790309 in scaling 2. Choosing randomly.
Mult

In [2]:
# new_results["00069_000690055"]
new_results["00039_000396799"]


{'ensemble': {'seed_0': 54,
  'seed_1': 80,
  'seed_2': 84,
  'seed_3': 54,
  'seed_4': 46,
  'seed_5': 116,
  'seed_6': 44,
  'seed_7': 62,
  'seed_8': 85,
  'seed_9': 73,
  'seed_10': 46,
  'seed_11': 41,
  'seed_12': 86,
  'seed_13': 60,
  'seed_14': 58,
  'seed_15': 57,
  'draw': False,
  'max_value': 41,
  'max_seed': 'seed_11',
  'min_value': 116,
  'min_seed': 'seed_5',
  'max_seed_2': 'seed_0',
  'max_value_2': 54,
  'min_seed_2': 'seed_1',
  'min_value_2': 80,
  'max_seed_4': 'seed_0',
  'max_value_4': 54,
  'min_seed_4': 'seed_2',
  'min_value_4': 84,
  'max_seed_8': 'seed_6',
  'max_value_8': 44,
  'min_seed_8': 'seed_5',
  'min_value_8': 116}}

In [3]:
with open("/root/BrushNet/runs/hyper_para/annotations/new_scores_with_ensemble_scaling.json", "w") as f:
    json.dump(new_results, f, indent=2)